In [3]:
# Tensorflow
import tensorflow as tf
from tensorflow.keras import layers, models, regularizers
from tensorflow.keras.metrics import Precision, Recall
from tensorflow.keras.optimizers import legacy
from tensorflow.keras.backend import clear_session
from tensorflow.python.ops import rnn, rnn_cell
from tensorflow.keras.callbacks import TensorBoard
import tensorflow as tf
from tensorboard.plugins.hparams import api as hp
import time


# Sklearn
from sklearn.metrics import confusion_matrix
from sklearn.model_selection import train_test_split, StratifiedKFold
from sklearn.preprocessing import StandardScaler, LabelEncoder
from sklearn.metrics import precision_score, recall_score


import matplotlib.pyplot as plt
import seaborn as sns
import os
import ast
import pandas as pd
import numpy as np

# from google.colab import drive

In [4]:
tf.keras.backend.clear_session()

In [5]:
%run Architectures.ipynb

In [6]:
# Hiperparâmetros a variar
epochs_list = [5, 10, 15]
batch_size_list = [32, 64, 128]
learning_rates = [0.0001, 0.0005, 0.001]
momentums = [0.8, 0.9, 0.95]
hidden_units_list = [64, 128, 256]
l2_lambdas = [0.0001, 0.001, 0.01]

In [7]:

# Defina os objetos HParam aqui
HP_NUM_EPOCHS = hp.HParam('epochs', hp.Discrete(epochs_list))
HP_BATCH_SIZE = hp.HParam('batch_size', hp.Discrete(batch_size_list))
HP_LEARNING_RATE = hp.HParam('learning_rate', hp.Discrete(learning_rates))
HP_MOMENTUM = hp.HParam('momentum', hp.Discrete(momentums))
HP_HIDDEN_UNITS = hp.HParam('hidden_units', hp.Discrete(hidden_units_list))
HP_L2_LAMBDA = hp.HParam('l2_lambda', hp.Discrete(l2_lambdas))

In [8]:
def best_hiperparameter_test(nn_type, mfcc, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units, tensorboard_callback):

    i = 1 #fold1 used for test

    # Define test set paths
    X_test_path = 'UrbanSound8K/audio/fold'+str(i)+'_4sec_mfccs_13/3D_array.npy'
    Y_test_path = 'UrbanSound8K/audio/fold'+str(i)+'_label/3D_array.npy'

    X_val_path1 = 'UrbanSound8K/audio/fold'+str((i+1-1) % 10 + 1)+f'_4sec_mfccs_{mfcc}/3D_array.npy'
    Y_val_path1 = 'UrbanSound8K/audio/fold'+str((i+1-1) % 10 + 1)+'_label/3D_array.npy'
    X_val_path2 = 'UrbanSound8K/audio/fold'+str((i+2-1) % 10 + 1)+f'_4sec_mfccs_{mfcc}/3D_array.npy'
    Y_val_path2 = 'UrbanSound8K/audio/fold'+str((i+2-1) % 10 + 1)+'_label/3D_array.npy'

    # Combine the validation paths
    X_val_paths = [X_val_path1, X_val_path2]
    Y_val_paths = [Y_val_path1, Y_val_path2]

    # # Define training set paths (all remaining folds)
    X_train_paths = ['UrbanSound8K/audio/fold'+str((j-1) % 10 + 1)+f'_4sec_mfccs_{mfcc}/3D_array.npy' for j in range(i+3, i+10)]
    Y_train_paths = ['UrbanSound8K/audio/fold'+str((j-1) % 10 + 1)+'_label/3D_array.npy' for j in range(i+3, i+10)]

    # Define test set paths
    X_test_path = f'UrbanSound8K/audio/fold{i}_4sec_mfccs_{mfcc}/3D_array.npy'
    Y_test_path = f'UrbanSound8K/audio/fold{i}_label/3D_array.npy'

    # Define validation set paths (wrapping around if i+2 > 10)
    X_val_path1 = f'UrbanSound8K/audio/fold{((i+1-1) % 10 + 1)}_4sec_mfccs_{mfcc}/3D_array.npy'
    Y_val_path1 = f'UrbanSound8K/audio/fold{((i+1-1) % 10 + 1)}_label/3D_array.npy'
    X_val_path2 = f'UrbanSound8K/audio/fold{((i+2-1) % 10 + 1)}_4sec_mfccs_{mfcc}/3D_array.npy'
    Y_val_path2 = f'UrbanSound8K/audio/fold{((i+2-1) % 10 + 1)}_label/3D_array.npy'

    # Combine the validation paths
    X_val_paths = [X_val_path1, X_val_path2]
    Y_val_paths = [Y_val_path1, Y_val_path2]

    # Define training set paths (all remaining folds)
    X_train_paths = [f'UrbanSound8K/audio/fold{((j-1) % 10 + 1)}_4sec_mfccs_{mfcc}/3D_array.npy' for j in range(i+3, i+11)]
    Y_train_paths = [f'UrbanSound8K/audio/fold{((j-1) % 10 + 1)}_label/3D_array.npy' for j in range(i+3, i+11)]

    # Load the datasets from the paths
    X_test = np.load(X_test_path)
    Y_test = np.load(Y_test_path)


    X_val1 = np.load(X_val_path1)
    X_val2 = np.load(X_val_path2)
    Y_val1 = np.load(Y_val_path1)
    Y_val2 = np.load(Y_val_path2)

    X_train = [np.load(path) for path in X_train_paths]
    Y_train = [np.load(path) for path in Y_train_paths]

    
    # Find the minimum size among all folds
    min_size = min([X_test.shape[0], X_val1.shape[0], X_val2.shape[0]] + [x.shape[0] for x in X_train])

    # Resize the data of each fold to the minimum size
    X_test_resized = X_test[:min_size]
    Y_test_resized = Y_test[:min_size]

    X_val1_resized = X_val1[:min_size]
    Y_val1_resized = Y_val1[:min_size]

    X_val2_resized = X_val2[:min_size]
    Y_val2_resized = Y_val2[:min_size]

    X_train_resized = [x[:min_size] for x in X_train]
    Y_train_resized = [y[:min_size] for y in Y_train]


    # Combine the validation sets
    X_test = X_test_resized
    Y_test = Y_test_resized
    X_val = np.concatenate((X_val1_resized, X_val2_resized), axis=2)
    Y_val = np.concatenate((Y_val1_resized, Y_val2_resized), axis=2)
    X_train = np.concatenate((X_train_resized[0], X_train_resized[1], X_train_resized[2], X_train_resized[3], X_train_resized[4], X_train_resized[5], X_train_resized[6]), axis=2)
    Y_train = np.concatenate((Y_train_resized[0], Y_train_resized[1], Y_train_resized[2], Y_train_resized[3], Y_train_resized[4], Y_train_resized[5], Y_train_resized[6]), axis=2)

    X_test = X_test.transpose(2,1,0)
    Y_test = Y_test.transpose(2,1,0)
    X_val = X_val.transpose(2,1,0)
    Y_val = Y_val.transpose(2,1,0)
    X_train = X_train.transpose(2,1,0)
    Y_train = Y_train.transpose(2,1,0)


#-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

    
    clear_session()  # Clear the previous model
    

    # Call de neural network
    input_shape = (751, mfcc)
    num_classes = 10

    #Neural Network Initialization
    if nn_type == "mlp":
        model = build_mlp_model(input_shape, num_classes, l2_lambda, n_hidden_units)

    elif nn_type == "rnn":
        model = build_rnn_model(input_shape, num_classes, l2_lambda, n_hidden_units)

    else:
        print("Introduce a valid neural network")





    model.summary() # print The neural network's architecture

    # Define the optimizer
    optimizer = legacy.SGD(learning_rate=learning_rate, momentum=momentum)

    #output layer
    model.add(layers.Dense(10, activation='softmax'))

    Y_train = np.squeeze(Y_train, axis=1)
    Y_val = np.squeeze(Y_val, axis=1)   



    # Compile the model.
    model.compile(
        optimizer=optimizer,
        loss='categorical_crossentropy',
        metrics=['accuracy']
    )


    history = model.fit(

        #training dataset
        X_train,
        Y_train,

        epochs=n_epochs,  # Number of epochs
        batch_size=batch_size, # Number of samples per batch

        #validation dataset
        validation_data=(X_val, Y_val),


        #callbacks
        callbacks=[tensorboard_callback]
    )

    # test_accuracy = model.evaluate(X_test, Y_test, verbose=0)[1]

    Y_train_classes = np.squeeze(Y_train).argmax(axis=-1) if Y_train.ndim == 3 else Y_train
    Y_val_classes = np.squeeze(Y_val).argmax(axis=-1) if Y_val.ndim == 3 else Y_val

    # Generate predictions
    Y_pred = model.predict(X_test)  # Predicted probabilities

    # Convert predictions to class labels
    Y_pred_classes = np.argmax(Y_pred, axis=-1)  # Convert probabilities to class labels

    # Flatten the one-hot encoded labels to 1D if they are 3D for Y_test
    Y_test_classes = np.squeeze(Y_test).argmax(axis=-1) if Y_test.ndim == 3 else Y_test

    # Make sure the confusion matrix function is correctly imported
    from sklearn.metrics import confusion_matrix

    # Calculate the confusion matrix
    conf_matrix = confusion_matrix(Y_test_classes, Y_pred_classes)

    # Evaluate the model, ensuring the Y_test used here matches the format expected by the model
    scores = model.evaluate(X_test, np.squeeze(Y_test), verbose=0)
    # Calculate precision and recall
    precision = precision_score(Y_test_classes, Y_pred_classes, average='macro')
    recall = recall_score(Y_test_classes, Y_pred_classes, average='macro')

    # Registre os hiperparâmetros e métricas no TensorBoard
    hparams = {
        'epochs': n_epochs,
        # 'batch_size': batch_size,
        # 'learning_rate': learning_rate,
        # 'momentum': momentum,
        # 'n_hidden_units': n_hidden_units,
        # 'l2_lambda': l2_lambda
    }
    run_name = f"run_{int(time.time())}"
    with tf.summary.create_file_writer(f'logs/hparam_tuning/{run_name}').as_default():
        hp.hparams(hparams)  # Registre os valores dos hiperparâmetros
        tf.summary.scalar('accuracy', scores[1], step=1)
        tf.summary.scalar('precision', precision, step=1)
        tf.summary.scalar('recall', recall, step=1)

    # Return the accuracy and the history
    return scores[1], history
    

In [7]:
def best_hiperparameter_main(nn_type, mfcc, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units):
    
    # General Confusion Matrix
    confusion_matrix_accumulated = np.zeros((10, 10))
    accuracies = []

    for i in range(1, 11):

        # Define test set paths
      # Define test set paths
        X_test_path = 'UrbanSound8K/audio/fold'+str(i)+'_4sec_mfccs_13/3D_array.npy'
        Y_test_path = 'UrbanSound8K/audio/fold'+str(i)+'_label/3D_array.npy'

        X_val_path1 = 'UrbanSound8K/audio/fold'+str((i+1-1) % 10 + 1)+f'_4sec_mfccs_{mfcc}/3D_array.npy'
        Y_val_path1 = 'UrbanSound8K/audio/fold'+str((i+1-1) % 10 + 1)+'_label/3D_array.npy'
        X_val_path2 = 'UrbanSound8K/audio/fold'+str((i+2-1) % 10 + 1)+f'_4sec_mfccs_{mfcc}/3D_array.npy'
        Y_val_path2 = 'UrbanSound8K/audio/fold'+str((i+2-1) % 10 + 1)+'_label/3D_array.npy'

        # Combine the validation paths
        X_val_paths = [X_val_path1, X_val_path2]
        Y_val_paths = [Y_val_path1, Y_val_path2]

        # # Define training set paths (all remaining folds)
        X_train_paths = ['UrbanSound8K/audio/fold'+str((j-1) % 10 + 1)+f'_4sec_mfccs_{mfcc}/3D_array.npy' for j in range(i+3, i+10)]
        Y_train_paths = ['UrbanSound8K/audio/fold'+str((j-1) % 10 + 1)+'_label/3D_array.npy' for j in range(i+3, i+10)]

        # Define test set paths
        X_test_path = f'UrbanSound8K/audio/fold{i}_4sec_mfccs_{mfcc}/3D_array.npy'
        Y_test_path = f'UrbanSound8K/audio/fold{i}_label/3D_array.npy'

        # Define validation set paths (wrapping around if i+2 > 10)
        X_val_path1 = f'UrbanSound8K/audio/fold{((i+1-1) % 10 + 1)}_4sec_mfccs_{mfcc}/3D_array.npy'
        Y_val_path1 = f'UrbanSound8K/audio/fold{((i+1-1) % 10 + 1)}_label/3D_array.npy'
        X_val_path2 = f'UrbanSound8K/audio/fold{((i+2-1) % 10 + 1)}_4sec_mfccs_{mfcc}/3D_array.npy'
        Y_val_path2 = f'UrbanSound8K/audio/fold{((i+2-1) % 10 + 1)}_label/3D_array.npy'

        # Combine the validation paths
        X_val_paths = [X_val_path1, X_val_path2]
        Y_val_paths = [Y_val_path1, Y_val_path2]

        # Define training set paths (all remaining folds)
        X_train_paths = [f'UrbanSound8K/audio/fold{((j-1) % 10 + 1)}_4sec_mfccs_{mfcc}/3D_array.npy' for j in range(i+3, i+11)]
        Y_train_paths = [f'UrbanSound8K/audio/fold{((j-1) % 10 + 1)}_label/3D_array.npy' for j in range(i+3, i+11)]

        # Load the datasets from the paths
        X_test = np.load(X_test_path)
        Y_test = np.load(Y_test_path)


        X_val1 = np.load(X_val_path1)
        X_val2 = np.load(X_val_path2)
        Y_val1 = np.load(Y_val_path1)
        Y_val2 = np.load(Y_val_path2)

        X_train = [np.load(path) for path in X_train_paths]
        Y_train = [np.load(path) for path in Y_train_paths]

        
        # Find the minimum size among all folds
        min_size = min([X_test.shape[0], X_val1.shape[0], X_val2.shape[0]] + [x.shape[0] for x in X_train])

        # Resize the data of each fold to the minimum size
        X_test_resized = X_test[:min_size]
        Y_test_resized = Y_test[:min_size]

        X_val1_resized = X_val1[:min_size]
        Y_val1_resized = Y_val1[:min_size]

        X_val2_resized = X_val2[:min_size]
        Y_val2_resized = Y_val2[:min_size]

        X_train_resized = [x[:min_size] for x in X_train]
        Y_train_resized = [y[:min_size] for y in Y_train]


        # Combine the validation sets
        X_test = X_test_resized
        Y_test = Y_test_resized
        X_val = np.concatenate((X_val1_resized, X_val2_resized), axis=2)
        Y_val = np.concatenate((Y_val1_resized, Y_val2_resized), axis=2)
        X_train = np.concatenate((X_train_resized[0], X_train_resized[1], X_train_resized[2], X_train_resized[3], X_train_resized[4], X_train_resized[5], X_train_resized[6]), axis=2)
        Y_train = np.concatenate((Y_train_resized[0], Y_train_resized[1], Y_train_resized[2], Y_train_resized[3], Y_train_resized[4], Y_train_resized[5], Y_train_resized[6]), axis=2)

        X_test = X_test.transpose(2,1,0)
        Y_test = Y_test.transpose(2,1,0)
        X_val = X_val.transpose(2,1,0)
        Y_val = Y_val.transpose(2,1,0)
        X_train = X_train.transpose(2,1,0)
        Y_train = Y_train.transpose(2,1,0)


    #-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------

        clear_session()  # Clear the previous model

        # Call de neural network
        input_shape = (751, mfcc)
        num_classes = 10

        #Neural Network Initialization
        if nn_type == "mlp":
            model = build_mlp_model(input_shape, num_classes, l2_lambda, n_hidden_units)

        elif nn_type == "rnn":
            model = build_rnn_model(input_shape, num_classes, l2_lambda, n_hidden_units)

        else:
            print("Introduce a valid neural network")


        model.summary() # print The neural network's architecture
        
        optimizer = legacy.SGD(learning_rate=learning_rate, momentum=momentum)

        #output layer
        model.add(layers.Dense(10, activation='softmax'))

        #fiz isto pq estava a dar erro e não sei porquê, mas funciona para rnn
        Y_train = np.squeeze(Y_train, axis=1)
        Y_val = np.squeeze(Y_val, axis=1)



        # Compile the model.
        model.compile(
            optimizer=optimizer,
            loss='categorical_crossentropy',
            metrics=['accuracy']
        )


        history = model.fit(

            #training dataset
            X_train,
            Y_train,

            epochs=n_epochs,  # Number of epochs
            batch_size=batch_size, # Number of samples per batch

            #validation dataset
            validation_data=(X_val, Y_val),

            #callbacks
            callbacks=[tensorboard_callback]
        )



    #-------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------------
        # Evaluate the model
        Y_train_classes = np.squeeze(Y_train).argmax(axis=-1) if Y_train.ndim == 3 else Y_train
        Y_val_classes = np.squeeze(Y_val).argmax(axis=-1) if Y_val.ndim == 3 else Y_val

        # Generate predictions
        Y_pred = model.predict(X_test)  # Predicted probabilities

        # Convert predictions to class labels
        Y_pred_classes = np.argmax(Y_pred, axis=-1)  # Convert probabilities to class labels

        # Flatten the one-hot encoded labels to 1D if they are 3D for Y_test
        Y_test_classes = np.squeeze(Y_test).argmax(axis=-1) if Y_test.ndim == 3 else Y_test

        # Calculate the confusion matrix
        conf_matrix = confusion_matrix(Y_test_classes, Y_pred_classes)

        #add confusion matrix
        confusion_matrix_accumulated += conf_matrix

        # Evaluate the model, ensuring the Y_test used here matches the format expected by the model
        scores = model.evaluate(X_test, np.squeeze(Y_test), verbose=0)
        print(f"Test accuracy for fold {i}:", scores[1])


        # Calculate precision and recall
        precision = precision_score(Y_test_classes, Y_pred_classes, average='macro')
        recall = recall_score(Y_test_classes, Y_pred_classes, average='macro')

       

        accuracies.append(scores[1])


    return scores[1], history
       




### MLP - Mfcc=13 - test function

In [28]:

# Melhor pontuação, parâmetros e histórico
best_score = 0
best_params = {}
best_history = None

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        #Create a unique directory for each run

                        # log_dir = "/Users/larasousa/Desktop/uni/ACII/Project_1/runs/" + f"run_{n_epochs}_{int(time.time())}"

                        log_dir = "/Users/larasousa/Desktop/uni/ACII/Project_1/runs/" + f"run_13{n_epochs}_{batch_size}_{learning_rate}_{momentum}_{n_hidden_units}_{l2_lambda}_{int(time.time())}"
                        tensorboard_callback = TensorBoard(log_dir=log_dir, histogram_freq=1)

                        # Pass the tensorboard callback to your training function
                        test_accuracy, history = best_hiperparameter_test("mlp", 13, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units, tensorboard_callback)
            
                        # Update best score, parameters, and history if current run is better
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            # best_params = {'n_epochs': n_epochs}
                            best_params = {'n_epochs': n_epochs, 'batch_size': batch_size, 'learning_rate': learning_rate, 'momentum': momentum, 'l2_lambda': l2_lambda, 'n_hidden_units': n_hidden_units}
                            best_history = history


# Exibir os melhores hiperparâmetros e pontuação
print("The best Hyperparameters: ", best_params)
print("The best score:", best_score)


# Abrindo o arquivo resultados.txt em modo de escrita
with open('results13.txt', 'w') as file:
    # Escrevendo no arquivo
    file.write("The best Hyperparameters: " + str(best_params) + "\n")
    file.write("The best score: " + str(best_score) + "\n")
                 

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 9763)              0         
                                                                 
 dense (Dense)               (None, 64)                624896    
                                                                 
 dropout (Dropout)           (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 64)                4160      
                                                                 
 dropout_1 (Dropout)         (None, 64)                0         
                                                                 
 dense_2 (Dense)             (None, 64)                4160      
                                                                 
 dense_3 (Dense)             (None, 10)                6

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Epoch 1/5
189/189 [==============================] - 1s 3ms/step - loss: 2.5707 - accuracy: 0.1148 - val_loss: 2.5788 - val_accuracy: 0.1103
Epoch 2/5
189/189 [==============================] - 0s 2ms/step - loss: 2.5691 - accuracy: 0.1166 - val_loss: 2.5771 - val_accuracy: 0.1103
Epoch 3/5
189/189 [==============================] - 0s 2ms/step - loss: 2.5719 - accuracy: 0.1163 - val_loss: 2.5410 - val_accuracy: 0.1771
Epoch 4/5
189/189 [==============================] - 0s 2ms/step - loss: 2.5617 - accuracy: 0.1201 - val_loss: 2.5307 - val_accuracy: 0.1782
Epoch 5/5
28/28 [==============================] - 0s 644us/step
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 9763)              0         
                                                                 
 dense (Dense)               (None, 64)                624896    
                     

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Epoch 1/5
189/189 [==============================] - 1s 3ms/step - loss: 4.8652 - accuracy: 0.1128 - val_loss: 4.8590 - val_accuracy: 0.1142
Epoch 2/5
189/189 [==============================] - 0s 2ms/step - loss: 4.8530 - accuracy: 0.1138 - val_loss: 4.8472 - val_accuracy: 0.1142
Epoch 3/5
189/189 [==============================] - 0s 2ms/step - loss: 4.8390 - accuracy: 0.1148 - val_loss: 4.8351 - val_accuracy: 0.1142
Epoch 4/5
189/189 [==============================] - 0s 2ms/step - loss: 4.8254 - accuracy: 0.1163 - val_loss: 4.8231 - val_accuracy: 0.1142
Epoch 5/5
28/28 [==============================] - 0s 605us/step
Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 9763)              0         
                                                                 
 dense (Dense)               (None, 128)               1249792   
                     

...

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 9763)              0         
                                                                 
 dense (Dense)               (None, 256)               2499584   
                                                                 
 dropout (Dropout)           (None, 256)               0         
                                                                 
 dense_1 (Dense)             (None, 256)               65792     
                                                                 
 dropout_1 (Dropout)         (None, 256)               0         
                                                                 
 dense_2 (Dense)             (None, 256)               65792     
                                                                 
 dense_3 (Dense)             (None, 10)                2

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 9763)              0         
                                                                 
 dense (Dense)               (None, 256)               2499584   
                                                                 
 dropout (Dropout)           (None, 256)               0         
                                                                 
 dense_1 (Dense)             (None, 256)               65792     
                                                                 
 dropout_1 (Dropout)         (None, 256)               0         
                                                                 
 dense_2 (Dense)             (None, 256)               65792     
                                                                 
 dense_3 (Dense)             (None, 10)                2

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


### MLP - Mfcc=25 - test function

In [9]:

# Melhor pontuação, parâmetros e histórico
best_score = 0
best_params = {}
best_history = None

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        #Create a unique directory for each run

                        # log_dir = "/Users/larasousa/Desktop/uni/ACII/Project_1/runs/" + f"run_{n_epochs}_{int(time.time())}"

                        log_dir = "/Users/larasousa/Desktop/uni/ACII/Project_1/runs/" + f"run_25{n_epochs}_{batch_size}_{learning_rate}_{momentum}_{n_hidden_units}_{l2_lambda}_{int(time.time())}"
                        tensorboard_callback = TensorBoard(log_dir=log_dir, histogram_freq=1)

                        # Pass the tensorboard callback to your training function
                        test_accuracy, history = best_hiperparameter_test("mlp", 25, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units, tensorboard_callback)
            
                        # Update best score, parameters, and history if current run is better
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            # best_params = {'n_epochs': n_epochs}
                            best_params = {'n_epochs': n_epochs, 'batch_size': batch_size, 'learning_rate': learning_rate, 'momentum': momentum, 'l2_lambda': l2_lambda, 'n_hidden_units': n_hidden_units}
                            best_history = history


# Exibir os melhores hiperparâmetros e pontuação
print("The best Hyperparameters: ", best_params)
print("The best score:", best_score)


# Abrindo o arquivo resultados.txt em modo de escrita
with open('results25.txt', 'w') as file:
    # Escrevendo no arquivo
    file.write("The best Hyperparameters: " + str(best_params) + "\n")
    file.write("The best score: " + str(best_score) + "\n")
                 

Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 18775)             0         
                                                                 
 dense (Dense)               (None, 64)                1201664   
                                                                 
 dropout (Dropout)           (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 64)                4160      
                                                                 
 dropout_1 (Dropout)         (None, 64)                0         
                                                                 
 dense_2 (Dense)             (None, 64)                4160      
                                                                 
 dense_3 (Dense)             (None, 10)                6

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 18775)             0         
                                                                 
 dense (Dense)               (None, 64)                1201664   
                                                                 
 dropout (Dropout)           (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 64)                4160      
                                                                 
 dropout_1 (Dropout)         (None, 64)                0         
                                                                 
 dense_2 (Dense)             (None, 64)                4160      
                                                                 
 dense_3 (Dense)             (None, 10)                6

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 18775)             0         
                                                                 
 dense (Dense)               (None, 64)                1201664   
                                                                 
 dropout (Dropout)           (None, 64)                0         
                                                                 
 dense_1 (Dense)             (None, 64)                4160      
                                                                 
 dropout_1 (Dropout)         (None, 64)                0         
                                                                 
 dense_2 (Dense)             (None, 64)                4160      
                                                                 
 dense_3 (Dense)             (None, 10)                6

...

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 18775)             0         
                                                                 
 dense (Dense)               (None, 256)               4806656   
                                                                 
 dropout (Dropout)           (None, 256)               0         
                                                                 
 dense_1 (Dense)             (None, 256)               65792     
                                                                 
 dropout_1 (Dropout)         (None, 256)               0         
                                                                 
 dense_2 (Dense)             (None, 256)               65792     
                                                                 
 dense_3 (Dense)             (None, 10)                2

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


Model: "sequential"
_________________________________________________________________
 Layer (type)                Output Shape              Param #   
 flatten (Flatten)           (None, 18775)             0         
                                                                 
 dense (Dense)               (None, 256)               4806656   
                                                                 
 dropout (Dropout)           (None, 256)               0         
                                                                 
 dense_1 (Dense)             (None, 256)               65792     
                                                                 
 dropout_1 (Dropout)         (None, 256)               0         
                                                                 
 dense_2 (Dense)             (None, 256)               65792     
                                                                 
 dense_3 (Dense)             (None, 10)                2

/Users/larasousa/.pyenv/versions/3.9.5/lib/python3.9/site-packages/sklearn/metrics/_classification.py:1469: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


### MLP - Mfcc=13 - main function

In [ ]:

# Melhor pontuação e parâmetros
best_score = 0
best_params = {}

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        # Chame sua função de teste aqui com os hiperparâmetros atuais
                        test_accuracy = best_hiperparameter_main("mlp", 13, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units)
                        
                        # Verifique se este modelo tem melhor pontuação
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            best_params = {
                                'n_epochs': n_epochs,
                                'batch_size': batch_size,
                                'learning_rate': learning_rate,
                                'momentum': momentum,
                                'n_hidden_units': n_hidden_units,
                                'l2_lambda': l2_lambda
                            }

# Exibir os melhores hiperparâmetros e pontuação
print("Melhores hiperparâmetros:", best_params)
print("Melhor pontuação:", best_score)


### MLP - Mfcc=25 - main function

In [ ]:
# Melhor pontuação e parâmetros
best_score = 0
best_params = {}

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        # Chame sua função de teste aqui com os hiperparâmetros atuais
                        test_accuracy = best_hiperparameter_main("mlp", 25, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units)
                        
                        # Verifique se este modelo tem melhor pontuação
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            best_params = {
                                'n_epochs': n_epochs,
                                'batch_size': batch_size,
                                'learning_rate': learning_rate,
                                'momentum': momentum,
                                'n_hidden_units': n_hidden_units,
                                'l2_lambda': l2_lambda
                            }

# Exibir os melhores hiperparâmetros e pontuação
print("Melhores hiperparâmetros:", best_params)
print("Melhor pontuação:", best_score)


### RNN - Mfcc=13 - test function

In [ ]:


# Melhor pontuação e parâmetros
best_score = 0
best_params = {}

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        # Chame sua função de teste aqui com os hiperparâmetros atuais
                        test_accuracy = best_hiperparameter_test("rnn", 13, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units)
                        
                        # Verifique se este modelo tem melhor pontuação
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            best_params = {
                                'n_epochs': n_epochs,
                                'batch_size': batch_size,
                                'learning_rate': learning_rate,
                                'momentum': momentum,
                                'n_hidden_units': n_hidden_units,
                                'l2_lambda': l2_lambda
                            }

# Exibir os melhores hiperparâmetros e pontuação
print("Melhores hiperparâmetros:", best_params)
print("Melhor pontuação:", best_score)


### RNN - Mfcc=25 - test function

In [ ]:


# Melhor pontuação e parâmetros
best_score = 0
best_params = {}

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        # Chame sua função de teste aqui com os hiperparâmetros atuais
                        test_accuracy = best_hiperparameter_test("rnn", 25, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units)
                        
                        # Verifique se este modelo tem melhor pontuação
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            best_params = {
                                'n_epochs': n_epochs,
                                'batch_size': batch_size,
                                'learning_rate': learning_rate,
                                'momentum': momentum,
                                'n_hidden_units': n_hidden_units,
                                'l2_lambda': l2_lambda
                            }

# Exibir os melhores hiperparâmetros e pontuação
print("Melhores hiperparâmetros:", best_params)
print("Melhor pontuação:", best_score)


### RNN - Mfcc=13 - main function

In [ ]:


# Melhor pontuação e parâmetros
best_score = 0
best_params = {}

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        # Chame sua função de teste aqui com os hiperparâmetros atuais
                        test_accuracy = best_hiperparameter_main("rnn", 13, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units)
                        
                        # Verifique se este modelo tem melhor pontuação
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            best_params = {
                                'n_epochs': n_epochs,
                                'batch_size': batch_size,
                                'learning_rate': learning_rate,
                                'momentum': momentum,
                                'n_hidden_units': n_hidden_units,
                                'l2_lambda': l2_lambda
                            }

# Exibir os melhores hiperparâmetros e pontuação
print("Melhores hiperparâmetros:", best_params)
print("Melhor pontuação:", best_score)


### RNN - Mfcc=25 - main function

In [ ]:


# Melhor pontuação e parâmetros
best_score = 0
best_params = {}

for n_epochs in epochs_list:
    for batch_size in batch_size_list:
        for learning_rate in learning_rates:
            for momentum in momentums:
                for n_hidden_units in hidden_units_list:
                    for l2_lambda in l2_lambdas:
                        # Chame sua função de teste aqui com os hiperparâmetros atuais
                        test_accuracy = best_hiperparameter_main("rnn", 25, n_epochs, batch_size, learning_rate, momentum, l2_lambda, n_hidden_units)
                        
                        # Verifique se este modelo tem melhor pontuação
                        if test_accuracy > best_score:
                            best_score = test_accuracy
                            best_params = {
                                'n_epochs': n_epochs,
                                'batch_size': batch_size,
                                'learning_rate': learning_rate,
                                'momentum': momentum,
                                'n_hidden_units': n_hidden_units,
                                'l2_lambda': l2_lambda
                            }

# Exibir os melhores hiperparâmetros e pontuação
print("Melhores hiperparâmetros:", best_params)
print("Melhor pontuação:", best_score)
